In [1]:
from matplotlib import pyplot as plt
import numpy as np
from scipy import signal as sig
import struct

import colorednoise

np.set_printoptions(linewidth=240)

In [2]:
%matplotlib widget

In [3]:
#colorednoise.powerlaw_psd_gaussian(1, int(1e4))

In [4]:
# From https://github.com/mubeta06/python/blob/master/signal_processing/sp/gold.py
preferred_pairs = {5:[[2],[1,2,3]], 6:[[5],[1,4,5]], 7:[[4],[4,5,6]],
                        8:[[1,2,3,6,7],[1,2,7]], 9:[[5],[3,5,6]], 
                        10:[[2,5,9],[3,4,6,8,9]], 11:[[9],[3,6,9]]}

def gen_gold(seq1, seq2):
    print(seq1.shape, seq2.shape)
    gold = [seq1, seq2]
    for shift in range(len(seq1)):
        gold.append(seq1 ^ np.roll(seq2, -shift))
    return gold

def gold(n):
    n = int(n)
    if not n in preferred_pairs:
        raise KeyError('preferred pairs for %s bits unknown' % str(n))
    t0, t1 = preferred_pairs[n]
    (seq0, _st0), (seq1, _st1) = sig.max_len_seq(n, taps=t0), sig.max_len_seq(n, taps=t1)
    return gen_gold(seq0, seq1)

In [16]:
fig, ax = plt.subplots()
ax.matshow(gold(5))

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

(31,) (31,)


In [17]:
def modulate(data, nbits=5, code=29):
    # 0, 1 -> -1, 1
    mask = gold(nbits)[code]*2 - 1
    
    # same here
    data_centered = (data*2 - 1)
    return (mask[:, np.newaxis] @ data_centered[np.newaxis, :] + 1).T.flatten() //2

In [18]:
def correlate(sequence, nbits=5, code=29, decimation=1, mask_filter=lambda x: x):
    # 0, 1 -> -1, 1
    mask = mask_filter(np.repeat(gold(nbits)[code]*2 -1, decimation))
    # center
    sequence -= np.mean(sequence)
    return np.correlate(sequence, mask, mode='full')

In [19]:
foo = modulate(np.array([0, 1, 0, 0, 1, 1, 1, 0])).astype(float)
fig, ax = plt.subplots()
ax.plot(correlate(foo))

(31,) (31,)


Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

(31,) (31,)


In [20]:
decimation = 10
signal_amplitude = 2.0
nbits = 5

foo = np.repeat(modulate(np.array([0, 1, 0, 0, 1, 1, 1, 0]), nbits) * 2.0 - 1, decimation) * signal_amplitude
noise = colorednoise.powerlaw_psd_gaussian(1, len(foo))

sosh = sig.butter(4, 0.01, btype='highpass', output='sos', fs=decimation)
sosl = sig.butter(6, 1.0, btype='lowpass', output='sos', fs=decimation)
filtered = sig.sosfilt(sosh, sig.sosfilt(sosl, foo + noise))
#filtered = sig.sosfilt(sosh, foo + noise)

fig, ((ax1, ax3), (ax2, ax4)) = plt.subplots(2, 2, figsize=(16, 9))
fig.tight_layout()

ax1.plot(foo + noise)
ax1.plot(foo)
ax1.set_title('raw')

ax2.plot(filtered)
ax2.plot(foo)
ax2.set_title('filtered')

ax3.plot(correlate(foo + noise, nbits=nbits, decimation=decimation))
ax3.set_title('corr raw')
 
ax3.grid()

ax4.plot(correlate(filtered, nbits=nbits, decimation=decimation))
ax4.set_title('corr filtered')
ax4.grid()

rms = lambda x: np.sqrt(np.mean(np.square(x)))
rms(foo), rms(noise)

(31,) (31,)


Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

(31,) (31,)
(31,) (31,)


(2.0, 1.0490216904842018)

In [21]:
with open('/mnt/c/Users/jaseg/shared/raw_freq.bin', 'rb') as f:
    mains_noise = np.copy(np.frombuffer(f.read(), dtype='float32'))
    print('mean:', np.mean(mains_noise))
    mains_noise -= np.mean(mains_noise)

mean: 49.98625


In [22]:
decimation = 10
signal_amplitude = 2.0e-3
nbits = 6

foo = np.repeat(modulate(np.array([0, 1, 0, 0, 1, 1, 1, 0]), nbits) * 2.0 - 1, decimation) * signal_amplitude
noise = np.resize(mains_noise, len(foo))

sosh = sig.butter(3, 0.01, btype='highpass', output='sos', fs=decimation)
sosl = sig.butter(3, 0.8, btype='lowpass', output='sos', fs=decimation)
#filtered = sig.sosfilt(sosh, sig.sosfilt(sosl, foo + noise))
filtered = sig.sosfilt(sosh, foo + noise)

cor1 = correlate(foo + noise, nbits=nbits, decimation=decimation)
cor2 = correlate(filtered, nbits=nbits, decimation=decimation)

cor2_pe = correlate(filtered, nbits=nbits, decimation=decimation, mask_filter=lambda mask: sig.sosfilt(sosh, sig.sosfiltfilt(sosl, mask)))

sosn = sig.butter(12, 4, btype='highpass', output='sos', fs=decimation)
#cor1_flt = sig.sosfilt(sosn, cor1)
#cor2_flt = sig.sosfilt(sosn, cor2)
#cor1_flt = cor1[1:] - cor1[:-1]
#cor2_flt = cor2[1:] - cor2[:-1]

fig, ((ax1, ax3, ax5), (ax2, ax4, ax6)) = plt.subplots(2, 3, figsize=(16, 9))
fig.tight_layout()

ax1.plot(foo + noise)
ax1.plot(foo)
ax1.set_title('raw')

ax2.plot(filtered)
ax2.plot(foo)
ax2.set_title('filtered')

ax3.plot(cor1)
ax3.set_title('corr raw')
ax3.grid()

ax4.plot(cor2)
ax4.set_title('corr filtered')
ax4.grid()

#ax5.plot(cor1_flt)
#ax5.set_title('corr raw (highpass)')
#ax5.grid()

#ax6.plot(cor2_flt)
#ax6.set_title('corr filtered (highpass)')
#ax6.grid()

ax6.plot(cor2_pe)
ax6.set_title('corr filtered w/ mask preemphasis')
ax6.grid()

rms = lambda x: np.sqrt(np.mean(np.square(x)))
rms(foo), rms(noise)

(63,) (63,)
(63,) (63,)
(63,) (63,)
(63,) (63,)


Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

(0.002, 0.012591236)

In [23]:
fig, ax = plt.subplots()

seq = np.repeat(gold(6)[29]*2 -1, decimation)
sosh = sig.butter(3, 0.01, btype='highpass', output='sos', fs=decimation)
sosl = sig.butter(3, 0.8, btype='lowpass', output='sos', fs=decimation)
seq_filtered = sig.sosfilt(sosh, sig.sosfiltfilt(sosl, seq))
#seq_filtered = sig.sosfilt(sosh, seq)

ax.plot(seq)
ax.plot(seq_filtered)

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

(63,) (63,)


In [24]:
fig, axs = plt.subplots(3, 1, figsize=(9, 7), sharex=True)
fig.tight_layout()
axs = axs.flatten()
for ax in axs:
    ax.grid()

seq = np.repeat(gold(6)[29]*2 -1, decimation)
sosh = sig.butter(3, 0.1, btype='highpass', output='sos', fs=decimation)
sosl = sig.butter(3, 0.8, btype='lowpass', output='sos', fs=decimation)
cor2_pe_flt = sig.sosfilt(sosh, cor2_pe)
cor2_pe_flt2 = sig.sosfilt(sosh, sig.sosfiltfilt(sosl, cor2_pe))

axs[0].plot(cor2_pe)
axs[1].plot(cor2_pe_flt)
axs[2].plot(cor2_pe_flt2)

#for idx in np.where(np.abs(cor2_pe_flt2) > 0.5)


Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

(63,) (63,)


In [49]:
threshold_factor = 5.0

import ipywidgets

cor_an = cor1

fig, (ax1, ax2, ax3) = plt.subplots(3, figsize=(12, 12))
fig.tight_layout()

ax1.matshow(sig.cwt(cor_an, sig.ricker, np.arange(1, 31)), aspect='auto')

for i in np.linspace(1, 10, 19):
    offx = 5*i
    ax2.plot(sig.cwt(cor_an, sig.ricker, [i]).flatten() + offx, color='red')

    ax2.text(-50, offx, f'{i:.1f}',
        horizontalalignment='right',
        verticalalignment='center',
        color='black')
ax2.grid()

ax3.grid()

cwt_res = sig.cwt(cor_an, sig.ricker, [7.3]).flatten()
line, = ax3.plot(cwt_res)
def update(w=10.0):
    line.set_ydata(sig.cwt(cor_an, sig.ricker, [w]).flatten())
    fig.canvas.draw_idle()
ipywidgets.interact(update)

import itertools
th = np.convolve(np.abs(cwt_res), np.ones((500,))/500, mode='same')
peaks = [ list(group) for val, group in itertools.groupby(enumerate(zip(th, cwt_res)), lambda elem: abs(elem[1][1]) > elem[1][0]*threshold_factor) if val ]
for group in peaks:
    pos = np.mean([idx for idx, _val in group])
    pol = np.mean([val for _idx, (_th, val) in group])
    ax3.axvline(pos, color='red', alpha=0.5)
    ax3.text(pos-20, 2.0, f'{0 if pol < 0 else 1}', horizontalalignment='right', verticalalignment='center', color='black')
    
ax3.plot(th)

<ipython-input-49-9776d553457e>:5: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  fig, (ax1, ax2, ax3) = plt.subplots(3, figsize=(12, 12))


Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

interactive(children=(FloatSlider(value=10.0, description='w', max=30.0, min=-10.0), Output()), _dom_classes=(…

In [27]:
fig, axs = plt.subplots(2, 1, figsize=(9, 7))
fig.tight_layout()
axs = axs.flatten()
for ax in axs:
    ax.grid()
    
axs[0].plot(cor2_pe_flt2[1::10] - cor2_pe_flt2[:-1:10])
a, b = cor2_pe_flt2[1::10] - cor2_pe_flt2[:-1:10], np.array([0.0, -0.5, 1.0, -0.5, 0.0])
axs[1].plot(np.convolve(a, b, mode='full'))

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …